# Problem : $$-\triangle u = f$$ with dirichlet boundary condition

In [ ]:
f_function(x, y) = 5*pi^2*sin(pi*x)*cos(2*pi*y)
bnd_u(x, y) = sin(pi*x)*cos(2*pi*y)

function GS(level, b, x, iter)
    length = 2^level-1
    h = 1/(2^level)
    n = length^2
    if level==1
        x[1] = (h^2)*b[1]/4
        return x
    end   
    for count = 1:iter
        for i = 1:n

In [1]:
            temp = 0
            if (i%length != 1)
                temp += x[i-1]*(-h^(-2))
            end
            if (i%length != 0)
                temp += x[i+1]*(-h^(-2))
            end
            if(i > length)
                temp += x[i-length]*(-h^(-2))
            end
            if(i <= n-length)
                temp += x[i+length]*(-h^(-2))
            end
            x[i] = (h^2)*(b[i]-temp)/4
        end
    end
    x
end

function multiA(level, x)
    length = 2^level-1
    h = 1/(2^level)
    n = length^2
    temp = 4*copy(x)
    for i in 1:length, j in 1:length
        nd = (i-1)*length+j
        if i!=1
            temp[nd] -= x[nd-length]
        end
        if i!=length
            temp[nd] -= x[nd+length]
        end
        if j!=1
            temp[nd] -= x[nd-1]
        end
        if j!=length
            temp[nd] -= x[nd+1]
        end
        temp[nd] = temp[nd]/(h^2)
    end
    temp
end      

multiA (generic function with 1 method)

In [2]:
function Prolongation(level, x)
    fine_length = 2^level-1
    coarse_length = 2^(level-1)-1
    Px = zeros(fine_length^2)
    for i in 1:coarse_length, j in 1:coarse_length
        coarse_nd = (i-1)*coarse_length+j
        fine_nd = (2i-1)*fine_length+2j
        Px[fine_nd] += x[coarse_nd]
        Px[fine_nd+1] += x[coarse_nd]/2
        Px[fine_nd-1] += x[coarse_nd]/2
        Px[fine_nd+fine_length] += x[coarse_nd]/2
        Px[fine_nd-fine_length] += x[coarse_nd]/2
        Px[fine_nd+fine_length+1] += x[coarse_nd]/4
        Px[fine_nd+fine_length-1] += x[coarse_nd]/4
        Px[fine_nd-fine_length+1] += x[coarse_nd]/4
        Px[fine_nd-fine_length-1] += x[coarse_nd]/4        
    end
    Px
end              
function Restriction(level, x)
    fine_length = 2^(level+1)-1
    coarse_length = 2^level-1
    Rx = zeros(coarse_length^2)
    for i in 1:coarse_length, j in 1:coarse_length
        coarse_nd = (i-1)*coarse_length+j
        fine_nd = (2i-1)*fine_length+2j
        Rx[coarse_nd] += x[fine_nd]/4
        Rx[coarse_nd] += x[fine_nd+1]/8
        Rx[coarse_nd] += x[fine_nd-1]/8
        Rx[coarse_nd] += x[fine_nd+fine_length]/8
        Rx[coarse_nd] += x[fine_nd-fine_length]/8
        Rx[coarse_nd] += x[fine_nd+fine_length+1]/16
        Rx[coarse_nd] += x[fine_nd+fine_length-1]/16
        Rx[coarse_nd] += x[fine_nd-fine_length+1]/16
        Rx[coarse_nd] += x[fine_nd-fine_length-1]/16
    end
    Rx
end

Restriction (generic function with 1 method)

In [3]:
function createR(max_level, min_level) 
    ## Returns restriction matrices, i.e. R[1] is (min_level+1)→(min_level) Restriction matrix
    ## Prolongation matrix P = transpose(4R)
    R = []
    for i = (min_level+1):max_level
        current_level = i
        current_length = 2^current_level-1
        next_level = i-1
        next_length = 2^next_level-1
        Rk = spzeros(next_length^2, current_length^2)
        for i in 1:next_length, j in 1:next_length
            next_nd = (i-1)*next_length+j
            fine_nd = (2i-1)*current_length+2j
            Rk[next_nd, fine_nd] += 1/4
            Rk[next_nd, fine_nd+1] += 1/8
            Rk[next_nd, fine_nd-1] += 1/8
            Rk[next_nd, fine_nd+current_length] += 1/8
            Rk[next_nd, fine_nd-current_length] += 1/8
            Rk[next_nd, fine_nd+current_length+1] += 1/16
            Rk[next_nd, fine_nd+current_length-1] += 1/16
            Rk[next_nd, fine_nd-current_length+1] += 1/16
            Rk[next_nd, fine_nd-current_length-1] += 1/16
        end
        push!(R, Rk)
    end
    R
end
function createA(max_level, min_level)
    ## Create A in Au = f (after max_level, Au = r)
    A = []
    for k = min_level:max_level
        length = 2^k-1
        hx = 1./(2^k)
        hy = 1./(2^k)
        Ak = spzeros(length^2, length^2)
        for i in 1:length, j in 1:length
            nd = (i-1)*length+j ## Translate (i, j) coordinate to node number in long vector
            Ak[nd, nd] += 2.*hx^(-2)+2.*hy^(-2)
            if i!=1
                Ak[nd, nd-length] += -hx^(-2)
            end
            if i!=length
                Ak[nd, nd+length] += -hx^(-2)
            end
            if j!=1
                Ak[nd, nd-1] += -hy^(-2)
            end
            if j!=length
                Ak[nd, nd+1] += -hy^(-2)
            end
        end
        push!(A, Ak)
    end
    A
end    

function createf(max_level, boundary_u, f_function)
    ## Create f for max_level
    length = 2^max_level-1
    hx = 1./(2^max_level)
    hy = 1./(2^max_level)
    f = zeros(length^2)
    ## Adding boundary condition(Dirichlet) 
    for i in 1:length, j in 1:length
        nd = (i-1)*length+j
        f[nd] += f_function(i*hx, j*hy)
        if i==1
            f[nd] += boundary_u(0, j*hy)*(hx^(-2))
        end
        if i==length
            f[nd] += boundary_u(1, j*hy)*(hx^(-2))
        end
        if j==1
            f[nd] += boundary_u(i*hx, 0)*(hy^(-2))
        end
        if j==length
            f[nd] += boundary_u(i*hx, 1)*(hy^(-2))
        end
    end
    f
end

createf (generic function with 1 method)

In [20]:
initial_level = 12
bottom_level = 1

println("Initializing conditions....")
x_sol = zeros((2^initial_level-1)^2)
initial_length = 2^initial_level-1
hx = 2.0^(-initial_level)
hy = 2.0^(-initial_level)
for i in 1:initial_length, j in 1:initial_length
    nd = (i-1)*initial_length+j
    x_sol[nd] = bnd_u(i*hx, j*hy)
end

## Initializing Au = f on finest grid
println("Initializing f....")
## A = createA(initial_level, bottom_level)
## R = createR(initial_level, bottom_level)
f = createf(initial_level, bnd_u, f_function)
println("Complete")

Initializing conditions....
Initializing f....
Complete


# Multigrid - Normal version

In [5]:
function multigrid_normal_V(initial_level, bottom_level, f, numgs)
    x = []
    r = []
    push!(x, rand((2^initial_level-1)^2))
    x[1] = GS(initial_level, f, x[1], numgs)
    r_temp = f-multiA(initial_level, x[1])
    save = norm(x[1]-x_sol)

    ## Going down to Coarsest grid
    for level = (initial_level-1):-1:(bottom_level)
        ## For each step, we do 3 things.
        ## First, restrict r of previous(finer) grid into current grid
        ## Second, GS Ax = r. Third, compute r_new = r - Ax. 
        ## Below is the list of indices of x, A, R, r for each level.
        ## index for x = initial_level - level + 1
        ## index for A = level - bottom_level + 1
        ## index for R = level - bottom_level
        ## index for r = intial_level - level   
        r_temp = Restriction(level, r_temp)
        x_temp = GS(level, r_temp, zeros((2.^level-1)^2), numgs)
        push!(r, r_temp)
        push!(x, x_temp)
        r_temp = r_temp - multiA(level, x_temp)
        ##r_temp = r_temp - A[level-bottom_level+1]*x_temp
        println("==== Going down ",level+1,"->",level," Complete ====")
    end

    ## Going up to Finest grid
    for level = (bottom_level+1):(initial_level-1)
        x_temp = Prolongation(level, x[initial_level-level+2]) ## Uprising x from the level below
        x[initial_level-level+1] += x_temp
        x[initial_level-level+1] = GS(level, r[initial_level-level], x[initial_level-level+1], numgs)
        println("==== Going up ", level-1,"->",level, " Complete ====")
    end

    ## Final step
    x[1] = x[1] + Prolongation(initial_level, x[2])
    println("==== Going up ", initial_level-1,"->",initial_level, " Complete ====")
    x[1] = GS(initial_level, f, x[1], numgs)
    x[1]
end

multigrid_normal_V (generic function with 1 method)

In [14]:
@time result = multigrid_normal_V(initial_level, bottom_level, f, 10);

==== Going down 10->9 Complete ====
==== Going down 9->8 Complete ====
==== Going down 8->7 Complete ====
==== Going down 7->6 Complete ====
==== Going down 6->5 Complete ====
==== Going down 5->4 Complete ====
==== Going down 4->3 Complete ====
==== Going down 3->2 Complete ====
==== Going down 2->1 Complete ====
==== Going up 1->2 Complete ====
==== Going up 2->3 Complete ====
==== Going up 3->4 Complete ====
==== Going up 4->5 Complete ====
==== Going up 5->6 Complete ====
==== Going up 6->7 Complete ====
==== Going up 7->8 Complete ====
==== Going up 8->9 Complete ====
==== Going up 9->10 Complete ====
  3.660481 seconds (334.16 M allocations: 5.052 GB, 7.05% gc time)


In [15]:
println("Max error : ",maximum(abs(result - x_sol)))
println("Error rate : ",norm(result-x_sol)/norm(x_sol))

Max error : 0.03001572662493679
Error rate : 0.0263496466018617


# W-cycle version

In [8]:
function multigrid_normal_W(initial_level, bottom_level, f, numgs)
    x = []
    r = []
    push!(x, rand((2^initial_level-1)^2))
    x[1] = GS(initial_level, f, x[1], numgs)
    r_temp = f-multiA(initial_level, x[1])
    save = norm(x[1]-x_sol)

    ## Going down to Coarsest grid
    for level = (initial_level-1):-1:(bottom_level)
        ## For each step, we do 3 things.
        ## First, restrict r of previous(finer) grid into current grid
        ## Second, GS Ax = r. Third, compute r_new = r - Ax. 
        ## Below is the list of indices of x, A, R, r for each level.
        ## index for x = initial_level - level + 1
        ## index for A = level - bottom_level + 1
        ## index for R = level - bottom_level
        ## index for r = intial_level - level   
        r_temp = Restriction(level, r_temp)
        x_temp = GS(level, r_temp, zeros((2.^level-1)^2), numgs)
        push!(r, r_temp)
        push!(x, x_temp)
        r_temp = r_temp - multiA(level, x_temp)
        ##r_temp = r_temp - A[level-bottom_level+1]*x_temp
        println("==== Going down ",level+1,"->",level," Complete ====")
    end

    ## Going up to Finest grid
    for level = (bottom_level+1):(initial_level-1)
        x_temp = Prolongation(level, x[initial_level-level+2]) ## Uprising x from the level below
        x[initial_level-level+1] += x_temp
        x[initial_level-level+1] = GS(level, r[initial_level-level], x[initial_level-level+1], numgs)
        println("==== Going up ", level-1,"->",level, " Complete ====")
    end

    ## Middle step
    x[1] += Prolongation(initial_level, x[2])
    x[1] = GS(initial_level, f, x[1], numgs)
    println("==== Going up ", initial_level-1,"->",initial_level, " Complete ====")
    println("==== V-cycle 1 complete ====")   
    x = [x[1]]
    r = []
    r_temp = f-multiA(initial_level, x[1])

    ## Going down to Coarsest grid
    for level = (initial_level-1):-1:(bottom_level)
        ## For each step, we do 3 things.
        ## First, restrict r of previous(finer) grid into current grid
        ## Second, GS Ax = r. Third, compute r_new = r - Ax. 
        ## Below is the list of indices of x, A, R, r for each level.
        ## index for x = initial_level - level + 1
        ## index for A = level - bottom_level + 1
        ## index for R = level - bottom_level
        ## index for r = intial_level - level   
        r_temp = Restriction(level, r_temp)
        x_temp = GS(level, r_temp, zeros((2.^level-1)^2), numgs)
        push!(r, r_temp)
        push!(x, x_temp)
        r_temp = r_temp - multiA(level, x_temp)
        ##r_temp = r_temp - A[level-bottom_level+1]*x_temp
        println("==== Going down ",level+1,"->",level," Complete ====")
    end

    ## Going up to Finest grid
    for level = (bottom_level+1):(initial_level-1)
        x_temp = Prolongation(level, x[initial_level-level+2]) ## Uprising x from the level below
        x[initial_level-level+1] += x_temp
        x[initial_level-level+1] = GS(level, r[initial_level-level], x[initial_level-level+1], numgs)
        println("==== Going up ", level-1,"->",level, " Complete ====")
    end

    ## Final step
    x[1] = x[1] + Prolongation(initial_level, x[2])
    println("==== Going up ", initial_level-1,"->",initial_level, " Complete ====")
    x[1] = GS(initial_level, f, x[1], numgs)
    x[1]
end

multigrid_normal_W (generic function with 1 method)

In [21]:
@time result = multigrid_normal_W(initial_level, bottom_level, f, 20);

==== Going down 12->11 Complete ====
==== Going down 11->10 Complete ====
==== Going down 10->9 Complete ====
==== Going down 9->8 Complete ====
==== Going down 8->7 Complete ====
==== Going down 7->6 Complete ====
==== Going down 6->5 Complete ====
==== Going down 5->4 Complete ====
==== Going down 4->3 Complete ====
==== Going down 3->2 Complete ====
==== Going down 2->1 Complete ====
==== Going up 1->2 Complete ====
==== Going up 2->3 Complete ====
==== Going up 3->4 Complete ====
==== Going up 4->5 Complete ====
==== Going up 5->6 Complete ====
==== Going up 6->7 Complete ====
==== Going up 7->8 Complete ====
==== Going up 8->9 Complete ====
==== Going up 9->10 Complete ====
==== Going up 10->11 Complete ====
==== Going up 11->12 Complete ====
==== V-cycle 1 complete ====
==== Going down 12->11 Complete ====
==== Going down 11->10 Complete ====
==== Going down 10->9 Complete ====
==== Going down 9->8 Complete ====
==== Going down 8->7 Complete ====
==== Going down 7->6 Complete ===

In [22]:
println("Max error : ",maximum(abs(result - x_sol)))
println("Error rate : ",norm(result-x_sol)/norm(x_sol))

Max error : 0.0001495128887339936
Error rate : 0.00013208144791653618
